# Počítačová algebra -- cvičení 4

## Úloha 1

In [ ]:
F = GF(1009) #takto lze zadefinovat těleso velikosti 1009 (protože je 1009 prvočíslo, tak je to rovno Z_1009)


In [5]:
a = F(158) #takto se Sage bude na a dívat jako na prvek tělesa F
print(a.is_primitive_root()) 
#a.is_primitive_root() vrací, zdali je a primitivní prvek. V tomto případě, je tedy odpověď ANO.

True


In [16]:
b = F(2)
print(b.multiplicative_order()) #multiplicative_order() vrací řád prvku v násobící grupě
#pozor, že .order() vrací řád prvku ve sčítací grupě, cože je něco jiného

504


In [17]:
#Počet primitivních prvků v Z_1009 je roven presně euler_phi(1008), kde euler_phi je Eulerova funkce 
#a 1008 je velikost multiplikativní grupy (pro více informací viz kurz Teorie čísel a Algebra)
print(euler_phi(1008))

288


In [15]:
#Kdyby člověku stačil náhodný primitivní prvek, tak jde získat například takto:
print(F.primitive_element())

11


## Úloha 2

In [24]:
"""Spočítá obecné FFT, viz skripta
-- n: počet koeficientů
-- omega: příslušná n-tá odmocnina z 1
-- coeffs: koeficienty 
"""

def FFT(n,omega,coeffs):
    if n == 1:
        return coeffs
    n2 = n//2
    b = FFT(n2, omega*omega,[coeffs[2*i] for i in range(n2)]) #Alternativně coeffs[::2]
    c = FFT(n2, omega*omega,[coeffs[2*i+1] for i in range(n2)]) #coeffs[1::2]
    res = [0 for i in range(n)]
    om_pow = 1
    for i in range(n2):
        temp = om_pow*c[i]
        res[i] = b[i]+temp
        res[n2+i] = b[i]-temp
        om_pow *= omega
    return res
        

In [28]:
P.<x> = GF(257)[]
f = 7*x^7+14*x^2+5

In [35]:
p = GF(257).primitive_element()
omega = p^32
print(omega)
print(omega.multiplicative_order())
#Takto dostaneme omega jako primitivní 8 odmocninu z jedné. POZOR, že samotný p použít nejde,
#neboť to není primitivní 8 odmocnina z 1

64
8


In [39]:
FFT(8,omega,f)

[26, 10, 103, 38, 12, 66, 136, 163]

In [40]:
#pro kontrolu:
[f(omega^i) for i in range(8)]

[26, 10, 103, 38, 12, 66, 136, 163]

In [ ]:
#POZOR, že při volbě jiné primitivní osmé odmocniny z jedné v GF(257) (v tomhle případě je to 64), to přirozeně vyjde jinak

## Úloha 3

In [38]:
#Inverzní FFT
def IFFT(n,omega,coeffs):
    inv = omega^(-1)
    return [(omega.parent()(n))^(-1)*elem for elem in FFT(n,inv,coeffs)] 
#omega.parent() najde okruh ze kterého je omega, aby v něm mohla invertovat n

In [44]:
P(IFFT(8,omega,[26, 10, 103, 38, 12, 66, 136, 163]))

7*x^7 + 14*x^2 + 5

## Úloha 4

In [46]:
"""Funkce pro násobení dvou celočíselných polynomů za použítí komplexních odmocnin z 1
-- f,g: libovolné polynomy
-- prec: počet bitů s jejichž přesností se počítá v komplexních číslech
"""
def mul_complex(f,g, prec = 64):
    C = ComplexField(prec)
    n = f.degree()+g.degree()+1
    n = 1 << n.nbits() #dosadí do n nejbližší větší mocninu 2 než (stupeň f + stupeň g)
    
    f_coeffs = f.coefficients(sparse=False)+[0] * (n - f.degree()-1) #doplní nulami koeficienty f a g do počtu n 
    g_coeffs = g.coefficients(sparse=False)+[0] * (n - g.degree()-1) #k získání koef. lze použít i např. f.list()
    omega = C(e^(2*pi*I/n)) #n-tá odmocnina z 1
    F = FFT(n,omega,f_coeffs)
    G = FFT(n,omega,g_coeffs)
    RES = [F[i]*G[i] for i in range(n)]
    res = IFFT(n,omega,RES)
    res = [item.real().round() for item in res] #vezme z komplexního čísla reálnou část a zaokrouhlí ji na nejbližší celé číslo
    return f.parent(res) #převede koeficienty zpátky do polynomu z původního oboru (ten je = f.parent())

In [72]:
Q.<t> = ZZ[]
prec = 10
f = Q.random_element(degree=10)
g = Q.random_element(degree=10)
print("polynom f: ",f)
print("polynom g: ",g)
a = mul_complex(f,g, prec=prec)
b = f*g
print(a)
print(b)
print(a==b)

#Při výše zvolené přesnosti ještě zdaleka ne vždy dává komplexní FFT správný výsledek

polynom f:  -t^10 + t^9 - 313*t^6 - t^5 - t^3 + t^2 + 2*t + 1
polynom g:  -t^10 - t^9 - t^8 + t^6 - t^5 + 231*t^4 - 4*t^3 - t - 3
19*t^30 - 21*t^29 - t^28 + 4*t^27 - 128*t^26 + 12*t^25 - 12*t^24 - 9*t^23 - 4*t^22 + 14*t^21 + 14*t^20 + 7*t^19 - 54*t^18 - 4*t^17 + 320*t^16 + 342*t^15 + 96*t^14 + 242*t^13 - 309*t^12 + 291*t^11 - 72064*t^10 + 996*t^9 + 8*t^8 + 72*t^7 + 1168*t^6 + 476*t^5 + 224*t^4 - 138*t^2 - 10*t + 12
t^20 - t^17 + 312*t^16 + 316*t^15 + 82*t^14 + 237*t^13 - 317*t^12 + 311*t^11 - 72304*t^10 + 1014*t^9 + 5*t^8 + 83*t^7 + 1174*t^6 + 460*t^5 + 224*t^4 - 2*t^3 - 5*t^2 - 7*t - 3
False


## Úloha 5

In [73]:
R.<s> = QQ[]
f = 1/3*s^3+1/5+1/6*s
print(f.denominator()) # takto se dá získat NSN všech jmenovatelů koeficientů polynomu

30


In [75]:
# Vynásobí dva racionální polynomy za pomocí komplexní odmocniny z 1 a FFT
def fast_mul_rat(f,g, prec=64):
    a = f.denominator()
    b = g.denominator()
    ff = (a*f).change_ring(ZZ)
    gg = (b*g).change_ring(ZZ)
    res = mul_complex(ff,gg,prec).change_ring(QQ)
    return res/(a*b)

In [77]:
R.<s> = QQ[]
f = 1/3*s^3+1/6*s+1/5
g =2*s^2+1/4
print(fast_mul_rat(f,g))
print(f*g)

2/3*s^5 + 5/12*s^3 + 2/5*s^2 + 1/24*s + 1/20
2/3*s^5 + 5/12*s^3 + 2/5*s^2 + 1/24*s + 1/20
